In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split, StratifiedKFold
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.nn.functional as F

# Stratified Train Test Split

In [2]:
# Importing pre-processed dataset
body_performance_df = pd.read_csv('processed_body_performance.csv')

In [3]:
output_dim = body_performance_df['class'].nunique()

In [4]:
# Acquiring target values and attributes
y = body_performance_df['class'].values
y = np.longlong(y)
X = body_performance_df.drop(columns=['class']).values
X = np.float32(X)
input_dim = X.shape[1] # NN input dimension = number of attributes

In [5]:
# Performing stratified train test split where test set is 30% of dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42, shuffle=True, stratify=y)

# Stratified K-fold Validation Split

In [6]:
# Defining a stratified 5-fold object to be used for cross-validation
# strat_k_fold = StratifiedKFold(n_splits=5, random_state=42, shuffle=True)

# Multi-Layered Perceptron (MLP)

In [7]:
class MLP_network(nn.Module):
    def __init__(self, input_dim=input_dim, hidden_dim=10, output_dim=output_dim):
        super(MLP_network, self).__init__()
        self.hidden1 = nn.Linear(input_dim, hidden_dim, bias=True)
        self.hidden2 = nn.Linear(hidden_dim, hidden_dim, bias=True)
        self.output = nn.Linear(hidden_dim, output_dim, bias=True)

    def forward(self, X):
        X = F.relu(self.hidden1(X))
        X = F.relu(self.hidden2(X))
        X = F.softmax(self.output(X), dim=-1) # sigmoid activation function is applied in loss function
        return X

In [8]:
class MLP_network(nn.Module):
    def __init__(self, input_dim=input_dim, hidden_dim=10, output_dim=output_dim, extra_hidden_layers=0):
        super().__init__()
        layers = []
        layers.append(nn.Linear(input_dim, hidden_dim, bias=True))
        layers.append(nn.ReLU())
        for i in range(extra_hidden_layers):
            layers.append(nn.Linear(hidden_dim, hidden_dim, bias=True))
            layers.append(nn.ReLU())
        layers.append(nn.Linear(hidden_dim, output_dim, bias=True))
        self.output = nn.Sequential(*layers)

    def forward(self, X):
        return F.softmax(self.output(X), dim=-1)

# Hyperparameter Tuning with Optuna

In [8]:
from skorch.classifier import NeuralNetClassifier
from skorch.callbacks import EarlyStopping
import optuna
from optuna.integration import SkorchPruningCallback
from sklearn.metrics import accuracy_score

In [9]:
#early_stopping = EarlyStopping(monitor='valid_acc', patience=10)

In [10]:
def objective(trial):
    
    hidden_dim = trial.suggest_int('hidden_dim', 4, input_dim*2)
    #extra_hidden_layers = trial.suggest_int('extra_hidden_layers', 0, 5)
    batch_size = trial.suggest_categorical('batch_size', [64, 128, 256, 512])
    learning_rate = trial.suggest_float('learning_rate', 0.0001, 0.1)
    weight_decay = trial.suggest_float('weight_decay', 0.0001, 0.1)
    smote_ratio = trial.suggest_float('smote_ratio', 0.6, 1.)
    max_epochs = trial.suggest_int('max_epochs', 50, 200, 10)

    
    torch.manual_seed(0)
    net = NeuralNetClassifier(
        MLP_network(),
        module__hidden_dim=hidden_dim,
        train_split=None,
        #module__extra_hidden_layers=extra_hidden_layers,
        optimizer=torch.optim.SGD,
        optimizer__momentum=0.9, # momentum set to commonly used value to save CPU time
        optimizer__lr=learning_rate,
        optimizer__weight_decay=weight_decay,
        max_epochs=max_epochs,
        batch_size=batch_size,
        callbacks=[SkorchPruningCallback(trial, 'valid_acc')],
    )
    
    
    net.fit(X_train, y_train)
    y_pred = net.predict(X_test)
    return accuracy_score(y_test, y_pred)

In [ ]:
pruner = optuna.pruners.MedianPruner(n_warmup_steps=30)
study = optuna.study.create_study(direction="maximize", pruner=pruner)
study.optimize(objective, n_trials=300)

[I 2022-04-30 11:35:41,247] A new study created in memory with name: no-name-53ac1560-e486-4e34-bab6-c40010097ec9


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1       11.6588       0.2501       11.9547  0.0900
      2       11.9568       0.2501       11.9547  0.0920
      3       11.9172       0.2501       11.9547  0.0860
      4        8.9789       0.2501        1.3869  0.0910
      5        1.3868       0.2496        1.3863  0.0890
      6        1.3866       0.2496        1.3864  0.0870
      7        1.3866       0.2496        1.3863  0.0900
      8        1.3866       0.2496        1.3863  0.0930
      9        1.3866       0.2496        1.3863  0.0870
     10        1.3866       0.2496        1.3863  0.0880
     11        1.3866       0.2496        1.3863  0.0860
     12        1.3866       0.2496        1.3863  0.0880
     13        1.3866       0.2496        1.3863  0.0970
     14        1.3866       0.2496        1.3863  0.0870
     15        1.3866       0.2496        1.3863  0.0880
     16        1.3866       0.2

[I 2022-04-30 11:35:54,123] Trial 0 finished with value: 0.2501244400199104 and parameters: {'hidden_dim': 15, 'batch_size': 256, 'learning_rate': 0.026977383114897155, 'weight_decay': 0.058610552540905636, 'smote_ratio': 0.6027945619856522, 'max_epochs': 140}. Best is trial 0 with value: 0.2501244400199104.


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        6.0197       0.2496        1.3888  0.1550
      2        1.3895       0.2496        1.3866  0.1510
      3        1.3890       0.2496        1.3866  0.1430
      4        1.3890       0.2496        1.3866  0.1460
      5        1.3890       0.2496        1.3866  0.1515
      6        1.3890       0.2496        1.3866  0.1570
      7        1.3890       0.2496        1.3866  0.1520
      8        1.3890       0.2496        1.3866  0.1550
      9        1.3890       0.2496        1.3866  0.1440
     10        1.3890       0.2496        1.3866  0.1520
     11        1.3890       0.2496        1.3866  0.1470
     12        1.3890       0.2496        1.3866  0.1540
     13        1.3890       0.2496        1.3866  0.1530
     14        1.3890       0.2496        1.3866  0.1595
     15        1.3890       0.2496        1.3866  0.1530
     16        1.3890       0.2

[I 2022-04-30 11:36:02,818] Trial 1 finished with value: 0.2501244400199104 and parameters: {'hidden_dim': 16, 'batch_size': 64, 'learning_rate': 0.08664193966304405, 'weight_decay': 0.06930987898608797, 'smote_ratio': 0.7458973739748833, 'max_epochs': 130}. Best is trial 0 with value: 0.2501244400199104.


...

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1       11.6209       0.2496       11.9632  0.0820
      2       11.9547       0.2496       11.9632  0.0810
      3       11.9742       0.2501       11.9547  0.0809
      4       11.2228       0.2501       11.9547  0.0780
      5       11.9525       0.2501       11.9547  0.0783
      6       11.9589       0.2501       11.9546  0.0810
      7        3.5966       0.2501        1.3926  0.0751
      8        1.3946       0.2304        1.3873  0.0822
      9        1.3871       0.2496        1.3865  0.0760
     10        1.3867       0.2501        1.3898  0.0800
     11        1.4908       0.2501        1.4095  0.0810
     12        1.3952       0.2501        1.3884  0.0790
     13        1.3884       0.2501        1.3863  0.0740
     14        1.3868       0.2795        1.3859  0.0780
     15        1.3868       0.2496        1.3864  0.0810
     16        1.3864       0.2

[I 2022-04-30 11:36:09,895] Trial 3 finished with value: 0.2501244400199104 and parameters: {'hidden_dim': 14, 'batch_size': 512, 'learning_rate': 0.09159185943162457, 'weight_decay': 0.06292361583240942, 'smote_ratio': 0.721248756496714, 'max_epochs': 70}. Best is trial 0 with value: 0.2501244400199104.


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1       11.5004       0.2501       11.9547  0.0920


[I 2022-04-30 11:36:10,134] Trial 4 finished with value: 0.2501244400199104 and parameters: {'hidden_dim': 13, 'batch_size': 256, 'learning_rate': 0.0438168347712547, 'weight_decay': 0.07422939373671196, 'smote_ratio': 0.6906991494390793, 'max_epochs': 110}. Best is trial 0 with value: 0.2501244400199104.


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1       11.8604       0.2501       11.9547  0.0830
      2       11.9568       0.2501       11.9547  0.0830
      3       11.9568       0.2501       11.9547  0.0830
      4        6.3555       0.2496        1.4339  0.0760
      5        1.3930       0.2501        1.3864  0.0770
      6        1.3863       0.2496        1.3864  0.0800
      7        1.3866       0.2496        1.3863  0.0830
      8        1.3866       0.2555        1.3829  0.0840
      9        1.3736       0.2501        1.3954  0.0870
     10        1.3915       0.2496        1.3871  0.0790
     11        1.3878       0.2501        1.3866  0.0830
     12        1.3864       0.2501        1.3865  0.0850
     13        1.3866       0.2496        1.3863  0.0810
     14        1.3866       0.2496        1.3863  0.0870
     15        1.3865       0.2496        1.3863  0.0850
     16        1.3865       0.2

In [ ]:
fig = optuna.visualization.plot_intermediate_values(study)
fig.show()

# Hyperparameter Grid Search

In [9]:
from skorch.classifier import NeuralNetClassifier
from sklearn.model_selection import GridSearchCV

In [10]:
torch.manual_seed(0)

net = NeuralNetClassifier(
    MLP_network,
    train_split=None,
    optimizer=torch.optim.SGD,
    optimizer__momentum=0.9 # momentum set to commonly used value to save CPU time
)

In [11]:
parameters = {
    'max_epochs': [10, 20, 30, 40, 50],
    'batch_size': [64, 128, 256], # batch-sizes are powers of 2
    'optimizer__lr': [0.001, 0.01, 0.1], # common values for learning rate
    'optimizer__weight_decay': [0.001, 0.01, 0.1], # common values for weight-decay factor
    'module__hidden_dim': [5, 10, 15, 20] # range of values less than twice the input dimension
}
gs = GridSearchCV(net, parameters, refit=False, cv=5, scoring='accuracy')
gs.fit(X_train, y_train)
print('Best-performing parameters:', gs.best_params_)
print('5-fold CV score:', gs.best_score_)

  epoch    train_loss     dur
-------  ------------  ------
      1        1.9336  0.1260
      2        1.4029  0.1150
      3        1.3951  0.1160
      4        1.3909  0.1210
      5        1.3888  0.1170
      6        1.3876  0.1140
      7        1.3870  0.1170
      8        1.3867  0.1210
      9        1.3866  0.1240
     10        1.3865  0.1240
  epoch    train_loss     dur
-------  ------------  ------
      1        1.6422  0.1200
      2        1.3916  0.1260
      3        1.3882  0.1190
      4        1.3870  0.1260
      5        1.3866  0.1223
      6        1.3865  0.1250
      7        1.3864  0.1195
      8        1.3864  0.1155
      9        1.3864  0.1200
     10        1.3864  0.1180
  epoch    train_loss     dur
-------  ------------  ------
      1        1.9784  0.1160
      2        1.3921  0.1194
      3        1.3891  0.1120
      4        1.3877  0.1160
      5        1.3870  0.1167
      6        1.3867  0.1176
      7        1.3865  0.1180
      8   

      6       11.9568  0.1300
      7       11.9568  0.1190
      8       11.9568  0.1230
      9       11.9568  0.1280
     10       11.9568  0.1240
  epoch    train_loss     dur
-------  ------------  ------
      1        1.4684  0.1170
      2        1.3870  0.1210
      3        1.3870  0.1250
      4        1.3870  0.1220
      5        1.3870  0.1220
      6        1.3870  0.1200
      7        1.3870  0.1210
      8        1.3870  0.1160
      9        1.3870  0.1220
     10        1.3870  0.1230
  epoch    train_loss     dur
-------  ------------  ------
      1        1.4059  0.1160
      2        1.3869  0.1240
      3        1.3869  0.1180
      4        1.3869  0.1200
      5        1.3869  0.1170
      6        1.3869  0.1260
      7        1.3869  0.1160
      8        1.3869  0.1240
      9        1.3869  0.1170
     10        1.3869  0.1200
  epoch    train_loss     dur
-------  ------------  ------
      1        1.4642  0.1160
      2        1.3869  0.1230
      3   

      6        1.3920  0.1200
      7        1.3920  0.1230
      8        1.3920  0.1180
      9        1.3920  0.1240
     10        1.3920  0.1170
  epoch    train_loss     dur
-------  ------------  ------
      1        1.3978  0.1240
      2        1.3895  0.1190
      3        1.3894  0.1240
      4        1.3894  0.1210
      5        1.3894  0.1315
      6        1.3894  0.1240
      7        1.3894  0.1170
      8        1.3894  0.1230
      9        1.3894  0.1270
     10        1.3894  0.1190
  epoch    train_loss     dur
-------  ------------  ------
      1        4.6504  0.1290
      2        1.4148  0.1240
      3        1.3910  0.1200
      4        1.3913  0.1240
      5        1.3913  0.1240
      6        1.3913  0.1200
      7        1.3913  0.1250
      8        1.3913  0.1180
      9        1.3913  0.1200
     10        1.3913  0.1200
  epoch    train_loss     dur
-------  ------------  ------
      1        2.3255  0.1150
      2        1.3903  0.1250
      3   

      8        1.1433  0.1460
      9        1.1384  0.1270
     10        1.1325  0.1300
  epoch    train_loss     dur
-------  ------------  ------
      1        1.4584  0.1280
      2        1.3787  0.1250
      3        1.3706  0.1270
      4        1.3571  0.1170
      5        1.1746  0.1240
      6        1.0437  0.1250
      7        1.0246  0.1260
      8        1.0004  0.1240
      9        0.9817  0.1210
     10        0.9706  0.1270
  epoch    train_loss     dur
-------  ------------  ------
      1        1.3976  0.1270
      2        1.3868  0.1310
      3        1.3869  0.1250
      4        1.3869  0.1170
      5        1.3869  0.1360
      6        1.3869  0.1330
      7        1.3869  0.1230
      8        1.3869  0.1200
      9        1.3869  0.1310
     10        1.3869  0.1210
  epoch    train_loss     dur
-------  ------------  ------
      1       11.9361  0.1240
      2       11.9547  0.1275
      3       11.9547  0.1320
      4       11.9547  0.1290
      5   

      5       11.9568  0.1310
      6       11.9568  0.1300
      7       11.9568  0.1200
      8       11.9568  0.1330
      9       11.9568  0.1300
     10       11.9568  0.1320
  epoch    train_loss     dur
-------  ------------  ------
      1       11.9072  0.1280
      2        5.7438  0.1290
      3        1.3899  0.1210
      4        1.3900  0.1200
      5        1.3900  0.1240
      6        1.3900  0.1250
      7        1.3900  0.1190
      8        1.3900  0.1230
      9        1.3900  0.1150
     10        1.3900  0.1210
  epoch    train_loss     dur
-------  ------------  ------
      1       11.9382  0.1190
      2       11.9568  0.1240
      3        9.3312  0.1190
      4        1.3920  0.1350
      5        1.3913  0.1300
      6        1.3913  0.1180
      7        1.3913  0.1200
      8        1.3913  0.1220
      9        1.3913  0.1240
     10        1.3913  0.1240
  epoch    train_loss     dur
-------  ------------  ------
      1       11.8286  0.1170
      2   

...

     23       11.9589  0.0680
     24       11.9589  0.0920
     25       11.9589  0.0710
     26       11.9589  0.0710
     27       11.9589  0.0720
     28       11.9589  0.0690
     29       11.9589  0.0810
     30       11.9589  0.0680
     31       11.9589  0.0710
     32       11.9589  0.0690
     33       11.9589  0.0730
     34       11.9589  0.0700
     35       11.9589  0.0800
     36       11.9589  0.0710
     37       11.9589  0.0680
     38       11.9589  0.0720
     39       11.9589  0.0690
     40       11.9589  0.0680
     41       11.9589  0.0710
     42       11.9589  0.0710
     43       11.9589  0.0740
     44       11.9589  0.0690
     45       11.9589  0.0740
     46       11.9589  0.0720
     47       11.9589  0.0810
     48       11.9589  0.0720
     49       11.9589  0.0720
     50       11.9589  0.0690
  epoch    train_loss     dur
-------  ------------  ------
      1        2.9320  0.0680
      2        1.3868  0.0720
      3        1.3865  0.0670
      4   

     26        1.3864  0.0760
     27        1.3864  0.0680
     28        1.3864  0.0680
     29        1.3864  0.0710
     30        1.3864  0.0730
     31        1.3864  0.0730
     32        1.3864  0.0730
     33        1.3864  0.0690
     34        1.3864  0.0690
     35        1.3864  0.0690
     36        1.3864  0.0710
     37        1.3864  0.0700
     38        1.3864  0.0740
     39        1.3864  0.0670
     40        1.3864  0.0720
     41        1.3864  0.0650
     42        1.3864  0.0720
     43        1.3864  0.0690
     44        1.3864  0.0720
     45        1.3864  0.0710
     46        1.3864  0.0690
     47        1.3864  0.0750
     48        1.3864  0.0660
     49        1.3864  0.0780
     50        1.3864  0.0690
  epoch    train_loss     dur
-------  ------------  ------
      1       11.3626  0.0780
      2       11.9589  0.0750
      3       11.9589  0.0750
      4       11.9589  0.0670
      5        9.9994  0.0690
      6        1.3863  0.0690
      7   

     29       11.9568  0.0760
     30       11.9568  0.0810
     31       11.9568  0.0700
     32       11.9568  0.0780
     33       11.9568  0.0670
     34       11.9568  0.0690
     35       11.9568  0.0700
     36       11.9568  0.0750
     37       11.9568  0.0780
     38       11.9568  0.0700
     39       11.9568  0.0710
     40       11.9568  0.0750
     41       11.9568  0.0720
     42       11.9568  0.0690
     43       11.9568  0.0670
     44       11.9568  0.0690
     45       11.9568  0.0690
     46       11.9568  0.0750
     47       11.9568  0.0740
     48       11.9568  0.0670
     49       11.9568  0.0710
     50       11.9568  0.0750
  epoch    train_loss     dur
-------  ------------  ------
      1       11.6511  0.0700
      2       11.9547  0.0690
      3       11.9547  0.0710
      4       11.9547  0.0710
      5       11.9547  0.0740
      6       11.9547  0.0710
      7       11.9547  0.0710
      8       11.9547  0.0710
      9       11.9547  0.0670
     10   

     26        1.3880  0.0720
     27        1.3880  0.0720
     28        1.3880  0.0730
     29        1.3880  0.0730
     30        1.3880  0.0730
     31        1.3880  0.0760
     32        1.3880  0.0710
     33        1.3880  0.0730
     34        1.3880  0.0750
     35        1.3880  0.0780
     36        1.3880  0.0750
     37        1.3880  0.0710
     38        1.3880  0.0770
     39        1.3880  0.0730
     40        1.3880  0.0760
     41        1.3880  0.0740
     42        1.3880  0.0690
     43        1.3880  0.0700
     44        1.3880  0.0770
     45        1.3880  0.0730
     46        1.3880  0.0770
     47        1.3880  0.0800
     48        1.3880  0.0700
     49        1.3880  0.0750
     50        1.3880  0.0730
  epoch    train_loss     dur
-------  ------------  ------
      1       11.8571  0.0740
      2       11.9568  0.0730
      3       11.9568  0.0760
      4       11.9568  0.0790
      5       11.9568  0.0730
      6       11.9568  0.0750
      7   

     29        1.3880  0.0760
     30        1.3880  0.0650
     31        1.3880  0.0700
     32        1.3880  0.0680
     33        1.3880  0.0660
     34        1.3880  0.0720
     35        1.3880  0.0650
     36        1.3880  0.0710
     37        1.3880  0.0740
     38        1.3880  0.0730
     39        1.3880  0.0670
     40        1.3880  0.0660
     41        1.3880  0.0680
     42        1.3880  0.0660
     43        1.3880  0.0690
     44        1.3880  0.0740
     45        1.3880  0.0710
     46        1.3880  0.0780
     47        1.3880  0.0700
     48        1.3880  0.0690
     49        1.3880  0.0650
     50        1.3880  0.0720
  epoch    train_loss     dur
-------  ------------  ------
      1       11.8554  0.0680
      2        2.9084  0.0710
      3        1.8287  0.0660
      4        1.6243  0.0700
      5        1.4036  0.0690
      6        1.3966  0.0750
      7        1.3937  0.0680
      8        1.5420  0.0680
      9        1.4568  0.0770
     10   

In [ ]:
from skorch.callbacks import EarlyStopping

In [12]:
net_final = NeuralNetClassifier(
    MLP_network,
    optimizer=torch.optim.SGD,
    optimizer__momentum=0.9, # momentum set to commonly used value to save CPU time
    batch_size=128, 
    max_epochs=50, 
    module__hidden_dim=20,
    optimizer__lr=0.001,
    optimizer__weight_decay=0.01
)

In [13]:
net_final.fit(X_train, y_train)

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        2.2165       0.2768        1.3603  0.1090
      2        1.3335       0.3797        1.3036  0.1140
      3        1.2100       0.4912        1.1024  0.1140
      4        1.0894       0.5499        0.9972  0.1071
      5        0.9912       0.5717        0.9339  0.1128
      6        0.9732       0.5595        0.9309  0.1160
      7        0.9538       0.5840        0.9117  0.1150
      8        0.9421       0.5915        0.8982  0.1210
      9        0.9337       0.5947        0.8940  0.1230
     10        0.9290       0.5963        0.8908  0.1130
     11        0.9269       0.5877        0.8905  0.1170
     12        0.9243       0.5952        0.8870  0.1110
     13        0.9211       0.6048        0.8928  0.1110
     14        0.9177       0.6011        0.8934  0.1130
     15        0.9175       0.5941        0.8996  0.1140
     16        0.9142       0.6

<class 'skorch.classifier.NeuralNetClassifier'>[initialized](
  module_=MLP_network(
    (hidden1): Linear(in_features=11, out_features=20, bias=True)
    (hidden2): Linear(in_features=20, out_features=20, bias=True)
    (output): Linear(in_features=20, out_features=4, bias=True)
  ),
)

In [14]:
net_final.score(X_test, y_test)

0.606769537083126